## Higher Asymptotics of Lattice Path Walks on {N,S,E,W} Steps in a Quarter Plane
By Keith Ritchie and Stephen Melczer

Here we compute high-order asymptotic expansions for the number of lattice walks beginning at the origin of $\mathbb{Z}^2$, taking the steps $\{(\pm1,0),(0,\pm1)\}$, and staying in the non-negative quadrant $\mathbb{N}^2$. Details on why this computes the desired expansion can be found in Chapter 6 of [**An Invitation to Analytic Combinatorics**](https://melczer.ca/textbook/).

First we introduce necessary preliminaries, and define our function to compute asymptotic expansions.

In [1]:
# Define Weyl algebra (consisting of differentials and variables)
W.<t1,t2> = DifferentialWeylAlgebra(QQ);
dt1,dt2 = W.differentials()
var('T1 T2')

#Definition of application of differential operator.
def applyOp(Dop,f):
    return sum([i[1]*T1^(i[0][0][0])*T2^(i[0][0][1])*diff(f,T1,i[0][1][0],T2,i[0][1][1]) for i in Dop.list()])

#Define Psi function
Ps = -log(cos(T1)+cos(T2)) + log(2) - (T1^2+T2^2)/4

#Define P functions for rho = 1 (P1) and rho = -1 (P2)
P1 = (1 + e^(i*T1))*(1 + e^(i*T2))
P2 = (1 - e^(i*T1))*(1 - e^(i*T2))

#Define differential operator Epsilon.
Epsilon = (-2)*(dt1^2+dt2^2)

# Define variables and assumptions
var('l j n')
assume(l>0, j>0, n>0)
assume(l, 'integer', j, 'integer', n, 'integer')

#Sequence of powers of Epsilon applied to f*P1 for arbitrary l at (0,0)
def a1(p,l):
    return applyOp(Epsilon^p, Ps^l*P1).subs(T1=0,T2=0)

#Sequence of powers of Epsilon applied to f*P2 for arbitrary l at (0,0)
def a2(p,l):
    return applyOp(Epsilon^p, Ps^l*P2).subs(T1=0,T2=0)

#Define Kj terms for rho = 1 and rho = -1 as a sequence in j following the general construction on page 234.
def Kj1(j):
    return (-1)^j *sum(a1(l+j,l)/(2^(j+l)*factorial(l)*factorial(j+l)) for l in (0..2*j))

def Kj2(j):
    return (-1)^j *sum(a2(l+j,l)/(2^(j+l)*factorial(l)*factorial(j+l)) for l in (0..2*j))

#Define expression for asymptotics of Cn as a function of M, a natural number.
def Cn(M):
    return 4^n/(pi*n)*sum((Kj1(j)+Kj2(j)*(-1)^n)*n^(-j) for j in (0..M))


Next, we give some examples

In [2]:
# Generate first few expansions
ASM0 = Cn(0)
ASM1 = Cn(1)
show(ASM0)
show(ASM1)

4*4^n/(pi*n)

-2*4^n*(3/n - 2)/(pi*n)

In [3]:
# Take order two expansion
ASM2 = Cn(2)
show(ASM2)

1/2*4^n*((2*(-1)^n + 19)/n^2 - 12/n + 8)/(pi*n)

We check our formulas by comparing them to numerically generated data.

In [4]:
# Let's check our formula
# Code to generate number of walks of length n
@CachedFunction 
def WalksIJ(i,j,n):
    if i<0 or j<0:
        return 0
    elif n==0 and i==0 and j==0:
        return 1
    elif n==0:
        return 0
    else:
        return WalksIJ(i-1,j,n-1) + WalksIJ(i+1,j,n-1) + WalksIJ(i,j-1,n-1) + WalksIJ(i,j+1,n-1)
    
def Walks(n): 
    return sum([WalksIJ(i,j,n) for i in range(n+1) for j in range(n+1)])

# Test code
[Walks(k) for k in range(10)]

[1, 2, 6, 18, 60, 200, 700, 2450, 8820, 31752]

In [5]:
# Pretty close already at n=10
print(Walks(10))
print(ASM2.subs(n=10).n())

116424
116987.123578877


Each successive expansion adds about one decimal place of accuracy when $n=20$, as expected.

In [6]:
print(ASM0.subs(n=20).n()/Walks(20))
print(ASM1.subs(n=20).n()/Walks(20))
print(ASM2.subs(n=20).n()/Walks(20))

1.07412849449210
0.993568857405193
1.00061782565030
